In [1]:
import json
import math
import os
import sys
from typing import Dict, Union, Callable, Tuple, Optional

import bpy
import mathutils
import numpy as np

In [2]:
list(bpy.data.objects)

[bpy.data.objects['Camera'],
 bpy.data.objects['Cube'],
 bpy.data.objects['Light']]

In [3]:
json_file_path = "/home/yizhou/Research/temp/2.txt"

In [4]:
args = json.loads(open(json_file_path).read())

In [5]:
args

{'data': [{'type': 'front3d',
   'houseLayoutFile': '/home/yizhou/Research/temp/Trescope/Trescope4Python/example/data/res/3D-FRONT-samples/scenes/310e0715-f95b-40ca-8edc-744560f57379.json',
   'shapeLocalSource': '/home/yizhou/Research/temp/Trescope/Trescope4Python/example/data/res/3D-FRONT-samples/3D-FUTURE-model',
   'shapeRemoteSource': {'objUrls': None, 'textureUrls': None},
   'view': None,
   'unit': 'm',
   'hiddenMeshes': ['Ceiling', 'SlabTop', 'ExtrusionCustomizedCeilingModel'],
   'renderType': 'color',
   'renderer': 'blender',
   'sampleCount': 128,
   'baseLightStrength': 8}],
 'layout': {'showlegend': True,
  'legend': {'orientation': 'h'},
  'yaxis': {'scaleanchor': 'x', 'scaleratio': 1},
  'margin': {'l': 60, 'r': 60, 't': 80, 'b': 60},
  'hoverlabel': {'namelength': -1},
  'scene': {'camera': {'eye': {'x': 2.0571141439246317,
     'y': 1.039072682672779,
     'z': -1.66250000190733},
    'up': {'x': 0, 'y': 1, 'z': 0},
    'center': {'x': 2.064691640650556,
     'y': 1

In [14]:
houseLayoutFile = "/home/yizhou/Research/3D_FRONT/3D-FRONT/00154c06-2ee2-408a-9664-b8fd74742897.json"

In [15]:
shapeLocalSource = "/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/"

In [16]:
#houseLayoutFile = args['data'][0]['houseLayoutFile']
#shapeLocalSource = args['data'][0]['shapeLocalSource']
renderType = args['data'][0]['renderType']
sampleCount = args['data'][0]['sampleCount']
baseLightStrength = args['data'][0]['baseLightStrength']
eye = args['layout']['scene']['camera']['eye']
center = args['layout']['scene']['camera']['center']
up = args['layout']['scene']['camera']['up']
fovy = args['layout']['scene']['camera']['fovy']
near, far = args['layout']['scene']['camera']['near'], args['layout']['scene']['camera']['far']
width, height = args['width'], args['height']
outputFile = args['outputFile']

In [17]:
houseLayoutFile

'/home/yizhou/Research/3D_FRONT/3D-FRONT/00154c06-2ee2-408a-9664-b8fd74742897.json'

In [18]:
with open(houseLayoutFile) as f: sceneDict = json.load(f)

In [19]:
sceneDict

{'uid': '00154c06-2ee2-408a-9664-b8fd74742897',
 'jobid': '',
 'design_version': '1587192194035_7b9b3e4e-f587-4cc2-90cd-6f60bc7f2582',
 'code_version': '0.11',
 'north_vector': [0, 1, 0],
 'furniture': [{'uid': '2958/model',
   'jid': 'a05567bc-4260-44b6-a4a7-3a3c9e11ed11',
   'aid': [],
   'title': 'window/bay window',
   'type': 'standard'},
  {'uid': '5682/model',
   'jid': '12b95733-764e-45bb-9278-86e740db1f32',
   'aid': [],
   'title': 'door/double sliding door',
   'type': 'standard'},
  {'uid': '10069/model',
   'jid': '097cf2fd-aa67-465c-88d3-9cf5a0f89cb3',
   'aid': [],
   'title': 'door/entry/double swing door - asymmetrical',
   'type': 'standard'},
  {'uid': '11159/model',
   'jid': '76b6d9d9-fb4c-49ba-a376-f01e59e480ea',
   'aid': [],
   'title': 'curtain/curtain',
   'type': 'standard'},
  {'uid': '2959/model',
   'jid': 'ff958559-245a-41c0-a33f-3d09872c023d',
   'aid': [],
   'title': 'window/floor-based window',
   'type': 'standard'},
  {'uid': '11903/model',
   'jid'

In [20]:
def __create_instance_table(sceneDict: Dict):
    _ = {'id': [], 'position': [], 'rotation': [], 'scale': [], 'ref': []}
    for room in sceneDict['scene']['room']:
        for child in room['children']:
            _['id'].append(child['instanceid'])
            _['position'].append(child['pos'])
            _['rotation'].append(child['rot'])
            _['scale'].append(child['scale'])
            _['ref'].append(child['ref'])
    return {key: np.array(value) for key, value in _.items()}

In [21]:
sceneDict['mesh'][0]

{'aid': [],
 'jid': '',
 'uid': '148451587192196201/0',
 'xyz': [-5.1615,
  2.6,
  -7.2521,
  -4.45692,
  2.15,
  -7.2521,
  -5.1615,
  0,
  -7.2521,
  -4.45692,
  2.15,
  -7.2521,
  -5.1615,
  2.6,
  -7.2521,
  -2.3581,
  2.6,
  -7.2521,
  -4.45692,
  2.15,
  -7.2521,
  -2.3581,
  2.6,
  -7.2521,
  -3.19628,
  2.15,
  -7.2521,
  -3.19628,
  2.15,
  -7.2521,
  -2.3581,
  2.6,
  -7.2521,
  -3.19628,
  0.45,
  -7.2521,
  -5.1615,
  0,
  -7.2521,
  -4.45692,
  0.45,
  -7.2521,
  -2.3581,
  0,
  -7.2521,
  -4.45692,
  0.45,
  -7.2521,
  -5.1615,
  0,
  -7.2521,
  -4.45692,
  2.15,
  -7.2521,
  -2.3581,
  0,
  -7.2521,
  -4.45692,
  0.45,
  -7.2521,
  -3.19628,
  0.45,
  -7.2521,
  -2.3581,
  0,
  -7.2521,
  -3.19628,
  0.45,
  -7.2521,
  -2.3581,
  2.6,
  -7.2521],
 'normal': [0,
  0,
  1,
  0,
  0,
  1,
  0,
  0,
  1,
  0,
  0,
  1,
  0,
  0,
  1,
  0,
  0,
  1,
  0,
  0,
  1,
  0,
  0,
  1,
  0,
  0,
  1,
  0,
  0,
  1,
  0,
  0,
  1,
  0,
  0,
  1,
  0,
  0,
  1,
  0,
  0,
  1,
  0,
  0

In [22]:
sceneDict['scene']['room'][1]['children']

[{'ref': '2958/model',
  'instanceid': 'furniture/130',
  'pos': [2.8812, 0.667, 4.9398],
  'rot': [0, 0, 0, 1],
  'scale': [1.21702, 1, 1]},
 {'ref': '180301587192199424/0',
  'pos': [0, 0, 0],
  'rot': [0, 0, 0, 1],
  'scale': [1, 1, 1],
  'instanceid': 'mesh/170'},
 {'ref': '165741587192199627/0',
  'pos': [0, 0, 0],
  'rot': [0, 0, 0, 1],
  'scale': [1, 1, 1],
  'instanceid': 'mesh/171'},
 {'ref': '166711587192199641/0',
  'pos': [0, 0, 0],
  'rot': [0, 0, 0, 1],
  'scale': [1, 1, 1],
  'instanceid': 'mesh/172'},
 {'ref': '162671587192199663/0',
  'pos': [0, 0, 0],
  'rot': [0, 0, 0, 1],
  'scale': [1, 1, 1],
  'instanceid': 'mesh/173'},
 {'ref': '163801587192199719/0',
  'pos': [0, 0, 0],
  'rot': [0, 0, 0, 1],
  'scale': [1, 1, 1],
  'instanceid': 'mesh/174'},
 {'ref': '162831587192201178/0',
  'pos': [0, 0, 0],
  'rot': [0, 0, 0, 1],
  'scale': [1, 1, 1],
  'instanceid': 'mesh/175'},
 {'ref': '162031587192201179/0',
  'pos': [0, 0, 0],
  'rot': [0, 0, 0, 1],
  'scale': [1, 1, 1]

In [23]:
instance_table = __create_instance_table(sceneDict)

In [24]:
def __create_mesh_table(sceneDict: Dict):
    _ = {'id': [], 'material_id': [], 'type': [], 'xyz': [], 'normal': [], 'uv': [], 'face': []}
    for index, mesh in enumerate(sceneDict['mesh']):
        _['id'].append(mesh['uid'])
        _['material_id'].append(mesh['material'])
        _['type'].append(mesh['type'])
        _['xyz'].append(np.array(mesh['xyz']).reshape(-1, 3).T.tolist())
        _['normal'].append(np.array(mesh['normal']).reshape(-1, 3).T.tolist())
        _['uv'].append(np.array(mesh['uv']).reshape(-1, 2).T.tolist())
        _['face'].append(np.array(mesh['faces']).reshape(-1, 3).T.tolist())
    return {key: np.array(value) for (key, value) in _.items()}

In [25]:
mesh_table = __create_mesh_table(sceneDict)

/home/yizhou/blender-2.92.0-linux64/blender:11: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.


In [26]:
def __create_material_table(sceneDict: Dict, material_when_unavailable: Union[int, Callable] = 0xffffffff):
    def compatible_texture(_material):
        if 'texture' not in _material: return ''
        _texture = _material['texture']
        return _texture['value'] if isinstance(_texture, dict) else _texture

    def compatible_color(rgba_or_rgb_array):
        r, g, b, a = rgba_or_rgb_array if 4 == len(rgba_or_rgb_array) else [*rgba_or_rgb_array, 255]
        return a << 24 | r << 16 | g << 8 | b

    def compatible_color_mode(_material):
        if not bool(_material.get('texture')): return 'color'
        if 'colorMode' in _material: return _material['colorMode']
        if bool(_material.get('useColor')): return 'color'
        return 'texture'

    def compatible_uv_transform(_material):
        return np.array(_material['UVTransform']).reshape(3, 3) if 'UVTransform' in _material else np.eye(3)

    _ = {'id': [], 'texture': [], 'color': [], 'colorMode': [], 'UVTransform': [], }
    for _material in sceneDict['material']:
        _['id'].append(_material['uid'])
        try:
            _['texture'].append(compatible_texture(_material['texture']))
            _['color'].append(compatible_color(_material['color']))
            _['colorMode'].append(compatible_color_mode(_material))
            _['UVTransform'].append(compatible_uv_transform(_material))
        except:
            if isinstance(material_when_unavailable, int):
                _['texture'].append('')
                _['UVTransform'].append(np.eye(3))
                _['color'].append(material_when_unavailable)
                _['colorMode'].append('color')
            else:
                _m = material_when_unavailable(_material)
                _['texture'].append(compatible_texture(_m['texture']))
                _['UVTransform'].append(compatible_uv_transform(_m))
                _['color'].append(compatible_color(_m['color']))
                _['colorMode'].append(compatible_color_mode(_m))
    return {key: np.array(value) for key, value in _.items()}


In [27]:
material_table = __create_material_table(sceneDict)

In [28]:
def __create_furniture_table(sceneDict: Dict):
    _ = {'id': [], 'jid': []}
    for furniture in sceneDict['furniture']:
        _['id'].append(furniture['uid'])
        _['jid'].append(furniture['jid'])
    return {key: np.array(value) for key, value in _.items()}

In [29]:
furniture_table = __create_furniture_table(sceneDict)

In [30]:
def join(ndarray1Dict, ndarray2Dict, c1, c2, rsuffix):
    leftColumnNames = list(ndarray1Dict.keys())
    rightColumnNames = list(ndarray2Dict.keys())

    def rightName(_name):
        return _name if _name not in leftColumnNames else f'{rsuffix}{_name}'

    columnNames = leftColumnNames + [rightName(name) for name in rightColumnNames]
    dict1KeyIndex = list(ndarray1Dict.keys()).index(c1)
    result = []
    for row1 in zip(*ndarray1Dict.values()):
        indices = (ndarray2Dict[c2] == row1[dict1KeyIndex])
        row_join = [v[indices] for v in ndarray2Dict.values()]
        for row2 in zip(*row_join): result.append([*row1, *row2])
    columns = np.array(result).T.tolist()
    return {name: column for name, column in zip(columnNames, columns)}

In [31]:
mesh_material = join(mesh_table, material_table, 'material_id', 'id', 'material_')
mesh_all = join(mesh_material, instance_table, 'id', 'ref', 'instance_')
furniture_all = join(furniture_table, instance_table, 'id', 'ref', 'instance_')

/home/yizhou/blender-2.92.0-linux64/blender:15: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.


In [32]:
def setSceneOutput(output_file_path, width, height):
    scene = bpy.context.scene
    scene.render.resolution_percentage = 100
    scene.render.resolution_x = width
    scene.render.resolution_y = height
    scene.render.filepath = output_file_path

In [33]:
setSceneOutput(outputFile, width, height)

In [34]:
def setCycles(num_samples=128):
    scene = bpy.context.scene
    scene.render.image_settings.file_format = 'PNG'
    scene.render.engine = 'CYCLES'
    scene.cycles.samples = num_samples
    scene.view_layers[0].cycles.use_denoising = True

In [35]:
setCycles(sampleCount)

In [36]:
def normalizeScene():
    for obj in bpy.data.objects:
        if obj.name not in ['Camera']: obj.select_set(state=True)
    bpy.ops.object.delete()

In [37]:
normalizeScene()

Info: Deleted 2 object(s)


In [38]:
def setCamera(eye, center, up, fovyDegree, near, far):
    camera = bpy.data.objects['Camera']

    camera.data.angle = math.radians(fovyDegree)

    eye = np.array(list(eye.values()))
    center = np.array(list(center.values()))
    north = np.array(list(up.values()))
    direction = center - eye
    forward = -direction / np.linalg.norm(direction)
    right = np.cross(north, forward)
    up = np.cross(forward, right)
    rotation = np.vstack([right, up, forward]).T
    matrix = np.eye(4)
    matrix[:3, :3] = rotation
    matrix[:3, -1] = eye
    mm = mathutils.Matrix.Identity(4)
    for index, row in enumerate(matrix): mm[index] = row
    camera.matrix_world = mm

    return camera, (eye, center)

In [39]:
_, (npEye, npCenter) = setCamera(eye, center, up, fovy, near, far)

In [40]:
def import_and_initialize_furniture(furniture, obj_and_texture_fetcher):
    jid, position, rotation, scale = furniture
    x, y, z, w = rotation
    rotation = (w, x, y, z)
    obj_path, texture_path = obj_and_texture_fetcher(jid)
    print(obj_path, obj_path is None, texture_path, texture_path is None)

    if obj_path is None or texture_path is None: return

    for obj in bpy.data.objects: obj.select_set(False)

    obj_material = add_material(f'obj_material[{jid}]', use_nodes=True, make_node_tree_empty=False)
    tree, links, nodes = obj_material.node_tree, obj_material.node_tree.links, obj_material.node_tree.nodes
    bsdf = nodes["Principled BSDF"]
    set_principled_node(principled_node=bsdf)
    texImage = nodes.new('ShaderNodeTexImage')
    texImage.image = bpy.data.images.load(texture_path)
    links.new(bsdf.inputs['Base Color'], texImage.outputs['Color'])

    bpy.ops.import_scene.obj(filepath=obj_path, axis_forward='Y', axis_up='Z')
    for model in bpy.context.selected_objects:
        model.select_set(False)
        model.name = f'{jid}.{model.name}'

        scaleMatrix = mathutils.Matrix.Identity(4)
        scaleMatrix[0][0], scaleMatrix[1][1], scaleMatrix[2][2] = scale
        model.matrix_world = (
                mathutils.Matrix.Translation(mathutils.Vector(position)) @
                mathutils.Quaternion(rotation).to_matrix().to_4x4() @
                scaleMatrix)

        if model.data.materials:
            model.data.materials[0] = obj_material
        else:
            model.data.materials.append(obj_material)


In [41]:
furniture_list = list(zip(furniture_all['jid'], furniture_all['position'], furniture_all['rotation'], furniture_all['scale']))

In [42]:
furniture = furniture_list[0]

In [43]:
furniture

('a05567bc-4260-44b6-a4a7-3a3c9e11ed11',
 array([2.8812, 0.667 , 4.9398]),
 array([0., 0., 0., 1.]),
 array([1.21702, 1.     , 1.     ]))

In [44]:
def add_material(name: str = "Material", use_nodes: bool = False, make_node_tree_empty: bool = False):
    material = bpy.data.materials.new(name)
    material.use_nodes = use_nodes
    if use_nodes and make_node_tree_empty: clean_nodes(material.node_tree.nodes)
    return material

In [45]:
def set_principled_node(
        principled_node,
        base_color: Tuple[float, float, float, float] = (0.6, 0.6, 0.6, 1.0),
        subsurface: float = 0.0,
        subsurface_color: Tuple[float, float, float, float] = (0.8, 0.8, 0.8, 1.0),
        subsurface_radius: Tuple[float, float, float] = (1.0, 0.2, 0.1),
        metallic: float = 0.0,
        specular: float = 0.5,
        specular_tint: float = 0.0,
        roughness: float = 0.5,
        anisotropic: float = 0.0,
        anisotropic_rotation: float = 0.0,
        sheen: float = 0.0,
        sheen_tint: float = 0.5,
        clearcoat: float = 0.0,
        clearcoat_roughness: float = 0.03,
        ior: float = 1.45,
        transmission: float = 0.0,
        transmission_roughness: float = 0.0) -> None:
    principled_node.inputs['Base Color'].default_value = base_color
    principled_node.inputs['Subsurface'].default_value = subsurface
    principled_node.inputs['Subsurface Color'].default_value = subsurface_color
    principled_node.inputs['Subsurface Radius'].default_value = subsurface_radius
    principled_node.inputs['Metallic'].default_value = metallic
    principled_node.inputs['Specular'].default_value = specular
    principled_node.inputs['Specular Tint'].default_value = specular_tint
    principled_node.inputs['Roughness'].default_value = roughness
    principled_node.inputs['Anisotropic'].default_value = anisotropic
    principled_node.inputs['Anisotropic Rotation'].default_value = anisotropic_rotation
    principled_node.inputs['Sheen'].default_value = sheen
    principled_node.inputs['Sheen Tint'].default_value = sheen_tint
    principled_node.inputs['Clearcoat'].default_value = clearcoat
    principled_node.inputs['Clearcoat Roughness'].default_value = clearcoat_roughness
    principled_node.inputs['IOR'].default_value = ior
    principled_node.inputs['Transmission'].default_value = transmission
    principled_node.inputs['Transmission Roughness'].default_value = transmission_roughness

In [46]:
for furniture in zip(furniture_all['jid'], furniture_all['position'], furniture_all['rotation'], furniture_all['scale']):
    jid, position, rotation, scale = furniture
    raw_model_path = os.path.join(shapeLocalSource, jid, 'raw_model.obj')
    texture_path = os.path.join(shapeLocalSource, jid, 'texture.png')
    print(raw_model_path, os.path.exists(raw_model_path))
    print(texture_path, os.path.exists(texture_path))
    
    import_and_initialize_furniture(furniture, lambda jid: (
        os.path.join(shapeLocalSource, jid, 'raw_model.obj') if os.path.exists(
            os.path.join(shapeLocalSource, jid, 'raw_model.obj')) else None,
        os.path.join(shapeLocalSource, jid, 'texture.png') if os.path.exists(
            os.path.join(shapeLocalSource, jid, 'texture.png')) else None,
    ))

/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/a05567bc-4260-44b6-a4a7-3a3c9e11ed11/raw_model.obj False
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/a05567bc-4260-44b6-a4a7-3a3c9e11ed11/texture.png False
None True None True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/12b95733-764e-45bb-9278-86e740db1f32/raw_model.obj False
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/12b95733-764e-45bb-9278-86e740db1f32/texture.png False
None True None True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/097cf2fd-aa67-465c-88d3-9cf5a0f89cb3/raw_model.obj False
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/097cf2fd-aa67-465c-88d3-9cf5a0f89cb3/texture.png False
None True None True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/ff958559-245a-41c0-a33f-3d09872c023d/raw_model.obj False
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/ff958559-245a-41c0-a33f-3d09872c023d/texture.png False
None True None True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/ff958559-245a-41c0-a33f-3d09872c023d/raw_model.ob

    (  0.0772 sec |   0.0761 sec) Done, loading materials and images...
WARNING, currently unsupported 'tr' translucency option, skipped.
WARNING, currently unsupported 'tf' filter color option, skipped.
WARNING, currently unsupported ambient texture, skipped.
    (  0.0785 sec |   0.0774 sec) Done, building geometries (verts:6149 faces:5675 materials: 1 smoothgroups:0) ...
    (  0.1169 sec |   0.1158 sec) Done.
  (  0.1178 sec |   0.1173 sec) Finished importing: '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/2bbc46d5-bbf7-40a0-87ac-bbcdb96d890e/raw_model.obj'
Progress: 100.00%

/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/2bbc46d5-bbf7-40a0-87ac-bbcdb96d890e/raw_model.obj True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/2bbc46d5-bbf7-40a0-87ac-bbcdb96d890e/texture.png True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/2bbc46d5-bbf7-40a0-87ac-bbcdb96d890e/raw_model.obj False /home/yizhou/Research/3D_FRONT/3D-FUTURE-model/2bbc46d5-bbf7-40a0-87ac-bbcdb96d890e/texture.png False
( 

    (  0.2311 sec |   0.2300 sec) Done.
  (  0.2319 sec |   0.2314 sec) Finished importing: '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/45039b73-7408-4cee-9a5e-c7b32456c775/raw_model.obj'
Progress: 100.00%

/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/ccd53884-ecdd-4a3b-a279-9fc18b6e4640/raw_model.obj False
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/ccd53884-ecdd-4a3b-a279-9fc18b6e4640/texture.png False
None True None True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/e40258de-5c0c-4ce7-8b85-2953d498ac77/raw_model.obj True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/e40258de-5c0c-4ce7-8b85-2953d498ac77/texture.png True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/e40258de-5c0c-4ce7-8b85-2953d498ac77/raw_model.obj False /home/yizhou/Research/3D_FRONT/3D-FUTURE-model/e40258de-5c0c-4ce7-8b85-2953d498ac77/texture.png False
(  0.0001 sec |   0.0001 sec) Importing OBJ '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/e40258de-5c0c-4ce7-8b85-2953d498ac77/raw_model.obj'...
  (  0

    (  0.0526 sec |   0.0517 sec) Done, loading materials and images...
WARNING, currently unsupported 'tr' translucency option, skipped.
WARNING, currently unsupported 'tf' filter color option, skipped.
WARNING, currently unsupported ambient texture, skipped.
    (  0.0540 sec |   0.0530 sec) Done, building geometries (verts:8347 faces:5178 materials: 1 smoothgroups:0) ...
    (  0.0859 sec |   0.0849 sec) Done.
  (  0.0867 sec |   0.0863 sec) Finished importing: '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/fc93abbf-984c-432a-abb7-7f1ce951955f/raw_model.obj'
Progress: 100.00%

/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/23716c11-4f82-4534-b744-e9e11e9912ec/raw_model.obj True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/23716c11-4f82-4534-b744-e9e11e9912ec/texture.png True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/23716c11-4f82-4534-b744-e9e11e9912ec/raw_model.obj False /home/yizhou/Research/3D_FRONT/3D-FUTURE-model/23716c11-4f82-4534-b744-e9e11e9912ec/texture.png False
( 

    (  0.1166 sec |   0.1155 sec) Done.
  (  0.1174 sec |   0.1169 sec) Finished importing: '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/24d58179-b687-4920-8652-a66745d787d7/raw_model.obj'
Progress: 100.00%

/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/24d58179-b687-4920-8652-a66745d787d7/raw_model.obj True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/24d58179-b687-4920-8652-a66745d787d7/texture.png True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/24d58179-b687-4920-8652-a66745d787d7/raw_model.obj False /home/yizhou/Research/3D_FRONT/3D-FUTURE-model/24d58179-b687-4920-8652-a66745d787d7/texture.png False
(  0.0001 sec |   0.0001 sec) Importing OBJ '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/24d58179-b687-4920-8652-a66745d787d7/raw_model.obj'...
  (  0.0005 sec |   0.0000 sec) Parsing OBJ file...
    (  0.0492 sec |   0.0483 sec) Done, loading materials and images...
WARNING, currently unsupported 'tr' translucency option, skipped.
WARNING, currently unsupported 'tf' filter

    (  0.2877 sec |   0.2866 sec) Done.
  (  0.2885 sec |   0.2881 sec) Finished importing: '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/06bb1295-131b-471a-8e97-66251b0f79fd/raw_model.obj'
Progress: 100.00%

/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/22c1b237-0364-4c1d-b9cf-83296265aaf9/raw_model.obj True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/22c1b237-0364-4c1d-b9cf-83296265aaf9/texture.png True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/22c1b237-0364-4c1d-b9cf-83296265aaf9/raw_model.obj False /home/yizhou/Research/3D_FRONT/3D-FUTURE-model/22c1b237-0364-4c1d-b9cf-83296265aaf9/texture.png False
(  0.0001 sec |   0.0001 sec) Importing OBJ '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/22c1b237-0364-4c1d-b9cf-83296265aaf9/raw_model.obj'...
  (  0.0008 sec |   0.0003 sec) Parsing OBJ file...
    (  0.0107 sec |   0.0096 sec) Done, loading materials and images...
WARNING, currently unsupported 'tr' translucency option, skipped.
WARNING, currently unsupported 'tf' filter

    (  0.3172 sec |   0.3161 sec) Done.
  (  0.3181 sec |   0.3175 sec) Finished importing: '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/41355b4d-e87a-4d7e-a0c5-a67340963ccc/raw_model.obj'
Progress: 100.00%

/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/487b28a6-b0ba-425c-bab9-23f1fa3b24eb/raw_model.obj True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/487b28a6-b0ba-425c-bab9-23f1fa3b24eb/texture.png True
/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/487b28a6-b0ba-425c-bab9-23f1fa3b24eb/raw_model.obj False /home/yizhou/Research/3D_FRONT/3D-FUTURE-model/487b28a6-b0ba-425c-bab9-23f1fa3b24eb/texture.png False
(  0.0001 sec |   0.0001 sec) Importing OBJ '/home/yizhou/Research/3D_FRONT/3D-FUTURE-model/487b28a6-b0ba-425c-bab9-23f1fa3b24eb/raw_model.obj'...
  (  0.0006 sec |   0.0002 sec) Parsing OBJ file...
    (  0.1048 sec |   0.1038 sec) Done, loading materials and images...
WARNING, currently unsupported 'tr' translucency option, skipped.
WARNING, currently unsupported 'tf' filter

In [47]:
def create_mesh(id_, xyz, normal, uv, face, color):
    def int_to_color_rgba_array(_color) -> Tuple[float, float, float, float]:
        _color_array = [(_color & 0x00ff0000) >> 16, (_color & 0x0000ff00) >> 8, (_color & 0x000000ff) >> 0, (_color & 0xff000000) >> 24, ]
        return tuple(map(lambda e: e / 255, _color_array))

    mesh_name = f'mesh_{id_}'
    new_mesh: bpy.types.Mesh = bpy.data.meshes.new(mesh_name)
    scene = bpy.context.scene
    vertices = xyz.T.tolist()
    faces = face.T.tolist()
    new_mesh.from_pydata(vertices, [], faces)
    new_mesh.update()

    new_object: bpy.types.Object = bpy.data.objects.new(f'{mesh_name}_obj', new_mesh)
    scene.collection.objects.link(new_object)

    new_object.location = (0, 0, 0)
    new_object.scale = (1, 1, 1)
    new_object.rotation_euler = (0, 0, 0)

    material = add_material(f'{mesh_name}_material', use_nodes=True, make_node_tree_empty=False)
    tree, links, nodes = material.node_tree, material.node_tree.links, material.node_tree.nodes

    bsdf = nodes["Principled BSDF"]
    base_color = int_to_color_rgba_array(color)
    set_principled_node(
        principled_node=bsdf,
        base_color=base_color
    )
    if new_object.data.materials:
        new_object.data.materials[0] = material
    else:
        new_object.data.materials.append(material)

    return new_object


# Set Mesh

In [48]:
for index, mesh in enumerate(
            zip(mesh_all['id'], mesh_all['type'], mesh_all['xyz'], mesh_all['normal'], mesh_all['uv'], mesh_all['face'], mesh_all['color'])):
        id_, type_, xyz, normal, uv, face, color = mesh
        xyz = np.array(xyz.tolist()).astype(np.float)
        normal = np.array(normal.tolist()).astype(np.float)
        uv = np.array(uv.tolist()).astype(np.float)
        face = np.array(face.tolist()).astype(np.int)
        create_mesh(id_, xyz, normal, uv, face, color)

/home/yizhou/blender-2.92.0-linux64/blender:4: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
/home/yizhou/blender-2.92.0-linux64/blender:5: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
/home/yizhou/blender-2.92.0-linux64/blender:6: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `flo

In [49]:
def createLightPoint(location: Tuple[float, float, float] = (0.0, 0.0, 5.0), strength: float = 100, name: Optional[str] = None) -> bpy.types.Object:
    bpy.ops.object.light_add(type='POINT', location=location)
    light = bpy.context.object.data
    light.energy = strength
    if name is not None: bpy.context.object.name = name
    return bpy.context.object

In [50]:
npDirection = npCenter - npEye
npDirection = npDirection / np.linalg.norm(npDirection)
for i in range(1, 4): createLightPoint(location=(npEye + npDirection * .5 * i).tolist(), strength=baseLightStrength)

In [ ]:
def startRender():
    bpy.ops.render.render(use_viewport=True, write_still=True)

In [ ]:
startRender()

In [ ]:
mesh_all['id']

In [ ]:
mesh_all_list = list(zip(mesh_all['id'], mesh_all['type'], mesh_all['xyz'], mesh_all['normal'], mesh_all['uv'], mesh_all['face'], mesh_all['color']))

In [ ]:
furniture_list